<a href="https://colab.research.google.com/github/ruthlys/.github/blob/main/Copy_of_EWS_yield_prediction_model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>



# Model Building for Early Warning System

# Introduction



Install the necessary libraries:

In [ ]:
pip install pandas geopandas shapely matplotlib pyproj


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 14.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 62.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.0/16.0 MB 49.9 MB/s eta 0:00:00


Load the CSV file with polygons from the onboarding exercise Season 1 and preview the dataset

In [ ]:
import pandas as pd
import geopandas as gpd
from shapely import wkt
import matplotlib.pyplot as plt


# Read the CSV file
df = pd.read_csv('onboarding1.csv')

df.head()


SubmissionDate                          start  \
0  2022-10-14T11:32:13.718Z  2022-10-14T14:20:46.830+03:00   
1  2022-10-14T11:31:13.418Z  2022-10-14T14:21:17.647+03:00   
2  2022-10-14T11:30:34.619Z  2022-10-14T14:21:25.769+03:00   
3  2022-10-14T11:30:23.024Z  2022-10-14T14:21:21.624+03:00   
4  2022-10-14T11:30:12.580Z  2022-10-14T14:20:52.095+03:00   

                             end username                  deviceid  \
0  2022-10-14T14:32:04.829+03:00      NaN  collect:wnkJ8A1gRm9cYN0O   
1  2022-10-14T14:31:04.892+03:00      NaN  collect:iUL9VElCefUJbh7q   
2  2022-10-14T14:30:24.333+03:00      NaN  collect:J0HuuQuHlK9Y45NA   
3  2022-10-14T14:30:10.233+03:00      NaN  collect:jwV9AeJanmRr6TDI   
4  2022-10-14T14:30:01.348+03:00      NaN  collect:rIWbIvZEiUyAyF4I   

  phonenumber Consent      Farmer_name  Gender Age_group  ...  \
0         NaN      OK     Agnes wawira  female   18___25  ...   
1         NaN      OK  Abijah karimi\n  female   45___55  ...   
2         NaN      OK  Virginia makena  female   36___45  ...   
3         NaN      OK   Bedan kithinji    male   26___35  ...   
4         NaN      OK            Njeru    male   26___35  ...   

                             meta-instanceID  \
0  uuid:298f11de-0c7b-4579-8eac-60b769ea9a44   
1  uuid:484352dc-70e3-4991-9f72-5d08c438a7f1   
2  uuid:7d8f4af0-82c2-4f04-9968-655e255def34   
3  uuid:53331ba2-8164-4d01-8d1c-35dde7c49169   
4  uuid:c23c57dd-ddb9-49cf-b4b7-0055cad4ae00   

                                         KEY  SubmitterID  \
0  uuid:298f11de-0c7b-4579-8eac-60b769ea9a44           81   
1  uuid:484352dc-70e3-4991-9f72-5d08c438a7f1           80   
2  uuid:7d8f4af0-82c2-4f04-9968-655e255def34           80   
3  uuid:53331ba2-8164-4d01-8d1c-35dde7c49169           82   
4  uuid:c23c57dd-ddb9-49cf-b4b7-0055cad4ae00           86   

            SubmitterName  AttachmentsPresent  AttachmentsExpected  Status  \
0            Agnes Wawira                   8                    8     NaN   
1  Abidjah Karimi Mwaniki                   8                    8     NaN   
2  Abidjah Karimi Mwaniki                   8                    8     NaN   
3  Bedan Kithinji Mwaniki                   8                    8     NaN   
4            Mike G Njeru                   7                    7     NaN   

  ReviewState                  DeviceID Edits  
0         NaN  collect:wnkJ8A1gRm9cYN0O     0  
1         NaN  collect:iUL9VElCefUJbh7q     0  
2         NaN  collect:J0HuuQuHlK9Y45NA     0  
3         NaN  collect:jwV9AeJanmRr6TDI     0  
4         NaN  collect:rIWbIvZEiUyAyF4I     0  

[5 rows x 49 columns]

In [ ]:
import pandas as pd

# Get unique values in a specific column
unique_values = df['ReviewState'].unique()

# Print the unique values
print(unique_values)


[nan 'hasIssues' 'edited' 'rejected']


In [ ]:
# Create a list of values you want to drop
values_to_drop = ['hasIssues', 'rejected']

# Filter the DataFrame to exclude rows with the specific values in the target column
df = df[~df['ReviewState'].isin(values_to_drop)]

df.head()


SubmissionDate                          start  \
0  2022-10-14T11:32:13.718Z  2022-10-14T14:20:46.830+03:00   
1  2022-10-14T11:31:13.418Z  2022-10-14T14:21:17.647+03:00   
2  2022-10-14T11:30:34.619Z  2022-10-14T14:21:25.769+03:00   
3  2022-10-14T11:30:23.024Z  2022-10-14T14:21:21.624+03:00   
4  2022-10-14T11:30:12.580Z  2022-10-14T14:20:52.095+03:00   

                             end username                  deviceid  \
0  2022-10-14T14:32:04.829+03:00      NaN  collect:wnkJ8A1gRm9cYN0O   
1  2022-10-14T14:31:04.892+03:00      NaN  collect:iUL9VElCefUJbh7q   
2  2022-10-14T14:30:24.333+03:00      NaN  collect:J0HuuQuHlK9Y45NA   
3  2022-10-14T14:30:10.233+03:00      NaN  collect:jwV9AeJanmRr6TDI   
4  2022-10-14T14:30:01.348+03:00      NaN  collect:rIWbIvZEiUyAyF4I   

  phonenumber Consent      Farmer_name  Gender Age_group  ...  \
0         NaN      OK     Agnes wawira  female   18___25  ...   
1         NaN      OK  Abijah karimi\n  female   45___55  ...   
2         NaN      OK  Virginia makena  female   36___45  ...   
3         NaN      OK   Bedan kithinji    male   26___35  ...   
4         NaN      OK            Njeru    male   26___35  ...   

                             meta-instanceID  \
0  uuid:298f11de-0c7b-4579-8eac-60b769ea9a44   
1  uuid:484352dc-70e3-4991-9f72-5d08c438a7f1   
2  uuid:7d8f4af0-82c2-4f04-9968-655e255def34   
3  uuid:53331ba2-8164-4d01-8d1c-35dde7c49169   
4  uuid:c23c57dd-ddb9-49cf-b4b7-0055cad4ae00   

                                         KEY  SubmitterID  \
0  uuid:298f11de-0c7b-4579-8eac-60b769ea9a44           81   
1  uuid:484352dc-70e3-4991-9f72-5d08c438a7f1           80   
2  uuid:7d8f4af0-82c2-4f04-9968-655e255def34           80   
3  uuid:53331ba2-8164-4d01-8d1c-35dde7c49169           82   
4  uuid:c23c57dd-ddb9-49cf-b4b7-0055cad4ae00           86   

            SubmitterName  AttachmentsPresent  AttachmentsExpected  Status  \
0            Agnes Wawira                   8                    8     NaN   
1  Abidjah Karimi Mwaniki                   8                    8     NaN   
2  Abidjah Karimi Mwaniki                   8                    8     NaN   
3  Bedan Kithinji Mwaniki                   8                    8     NaN   
4            Mike G Njeru                   7                    7     NaN   

  ReviewState                  DeviceID Edits  
0         NaN  collect:wnkJ8A1gRm9cYN0O     0  
1         NaN  collect:iUL9VElCefUJbh7q     0  
2         NaN  collect:J0HuuQuHlK9Y45NA     0  
3         NaN  collect:jwV9AeJanmRr6TDI     0  
4         NaN  collect:rIWbIvZEiUyAyF4I     0  

[5 rows x 49 columns]

In [ ]:
df.columns

Index(['SubmissionDate', 'start', 'end', 'username', 'deviceid', 'phonenumber',
       'Consent', 'Farmer_name', 'Gender', 'Age_group',
       'Number_of_people_in_household', 'Number_of_children_under_5',
       'Farmer_s_Phone_number', 'geo_point-Latitude', 'geo_point-Longitude',
       'geo_point-Altitude', 'geo_point-Accuracy', 'polygon', 'intercropped',
       'primary_crop', 'primary_variety', 'primary_photo',
       'group_ou8zr01-primary_added_photo', 'secondary_crop',
       'secondary_variety', 'secondary_photo', 'secondary_added_photo',
       'secondary_added_photo_001', 'picture_field',
       'Which_inputs_have_been_applied',
       'Which_farm_activitie_nducted_on_the_field',
       'Which_DEMO_variety_has_been_issued',
       'Walk_to_the_centre_o_record_the_geo_point-Latitude',
       'Walk_to_the_centre_o_record_the_geo_point-Longitude',
       'Walk_to_the_centre_o_record_the_geo_point-Altitude',
       'Walk_to_the_centre_o_record_the_geo_point-Accuracy',
       'Wa

In [ ]:
print(df['polygon'].head())

0    -0.5298504 37.4531088 1377.4000244140625 3.55;...
1    -0.5298213 37.4530973 1377.4000244140625 2.433...
2    -0.5298605 37.4531083 1380.2000732421875 3.75;...
3    -0.5297978 37.4530367 1380.2000732421875 3.9;-...
4    -0.5298921 37.4531033 1377.4000244140625 3.9;-...
Name: polygon, dtype: object


Convert the polygon column into a geometry object.

In [ ]:
from shapely.geometry import Polygon

def string_to_polygon(coord_string):
    coords = coord_string.split(";")
    coords = [coord.split(" ") for coord in coords]

    # Remove empty strings and extra whitespaces
    coords = [[value.strip() for value in coord if value.strip() != ''] for coord in coords]

    # Ensure that we have at least two numeric values (latitude and longitude) for each coordinate
    coords = [coord[:2] for coord in coords if len(coord) >= 2 and coord[0].replace(".", "", 1).replace("-", "", 1).isdigit() and coord[1].replace(".", "", 1).replace("-", "", 1).isdigit()]

    # Convert the cleaned coordinate values to float
    coords = [(float(coord[1]), float(coord[0])) for coord in coords]

    return Polygon(coords)


Convert the dataframe into a geodataframe and calculate area under observation.

In [ ]:
import geopandas as gpd

# Assuming the polygon column is named 'polygon'
df['polygon'] = df['polygon'].apply(string_to_polygon)

# Convert the DataFrame to a GeoDataFrame
gdf = gpd.GeoDataFrame(df, geometry='polygon', crs="EPSG:4326")


Convert the polygons to UTM formats for accurate calculation of area

In [ ]:
longitude, latitude = gdf.geometry[0].centroid.coords[0]

utm_zone = int((longitude + 180) / 6) + 1
utm_crs = f"EPSG:326{utm_zone}" if latitude >= 0 else f"EPSG:327{utm_zone}"


In [ ]:
utm_crs

'EPSG:32737'

In [ ]:
gdf_utm = gdf.to_crs(utm_crs)


In [ ]:
gdf_utm.polygon

0      POLYGON ((327855.998 9941414.101, 327853.850 9...
1      POLYGON ((327854.717 9941417.318, 327854.673 9...
2      POLYGON ((327855.943 9941412.984, 327853.126 9...
3      POLYGON ((327847.971 9941419.915, 327847.971 9...
4      POLYGON ((327855.387 9941409.490, 327855.387 9...
                             ...                        
490    POLYGON ((254517.462 9864431.488, 254568.627 9...
491    POLYGON ((252411.231 9858584.818, 252400.600 9...
492    POLYGON ((254311.611 9856658.525, 254311.723 9...
493    POLYGON ((253907.958 9859781.081, 253912.176 9...
494    POLYGON ((254304.782 9856714.279, 254296.981 9...
Name: polygon, Length: 467, dtype: geometry

In [ ]:
# Calculate the area of each farm in square meters
gdf_utm['area_sqm'] = gdf_utm['polygon'].area

In [ ]:
total_area = gdf_utm['area_sqm'].sum()
print("Total area of the farms:", total_area, "square meters")


Total area of the farms: 4125157.6432829923 square meters


Visualize the plots from season 1

In [ ]:
import folium


In [ ]:
def gdf_to_geojson(gdf):
    geojson = gdf.to_crs(epsg='4326').to_json()
    return geojson


In [ ]:
farm_geojson = gdf_to_geojson(gdf)

In [ ]:
# Get the centroid of the GeoDataFrame to center the map
centroid = gdf.geometry.centroid[0].coords[:][0]

m = folium.Map(location=[centroid[1], centroid[0]], zoom_start=100, tiles="OpenStreetMap")


<ipython-input-26-962e74109efe>:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = gdf.geometry.centroid[0].coords[:][0]


In [ ]:
# Customize the style of the polygons, if desired
style_function = lambda x: {'fillColor': 'green', 'color': 'black'}

folium.GeoJson(farm_geojson, style_function=style_function).add_to(m)


In [ ]:
m


# Routine Analysis

In [ ]:
pip install rasterio geopandas matplotlib


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 34.4 MB/s eta 0:00:00


In [ ]:
import pandas as pd

# Read the farm_data.csv file
farm_data = pd.read_csv('routine1.csv')



In [ ]:
farm_data.columns


Index(['SubmissionDate', 'start', 'end', 'username', 'deviceid', 'phonenumber',
       'Consent', 'Farmer_s_Phone_number',
       'Walk_to_the_centre_o_record_the_geo_point-Latitude',
       'Walk_to_the_centre_o_record_the_geo_point-Longitude',
       'Walk_to_the_centre_o_record_the_geo_point-Altitude',
       'Walk_to_the_centre_o_record_the_geo_point-Accuracy',
       'Take_a_picture_of_a_ant_in_the_DEMO_PLOT',
       'Take_a_picture_of_the_DEMO_PLOT', 'geo_point-Latitude',
       'geo_point-Longitude', 'geo_point-Altitude', 'geo_point-Accuracy',
       'intercropped', 'primary_crop', 'primary_VC_photo', 'secondary_crop',
       'secondary_variety', 'secondary_VC_photo',
       'Which_inputs_have_be_since_the_last_visit',
       'Which_farm_activitie_since_the_last_visit', 'picture_field',
       'added_audio_info', 'meta-audit', 'meta-instanceID', 'KEY',
       'SubmitterID', 'SubmitterName', 'AttachmentsPresent',
       'AttachmentsExpected', 'Status', 'ReviewState', 'DeviceID', 

In [ ]:
# Merge farm_data with optimum_boundaries_gdf based on farm_id
merged_data = pd.merge(farm_data,gdf_utm, on='Farmer_s_Phone_number')

In [ ]:
merged_data.columns

Index(['SubmissionDate_x', 'start_x', 'end_x', 'username_x', 'deviceid_x',
       'phonenumber_x', 'Consent_x', 'Farmer_s_Phone_number',
       'Walk_to_the_centre_o_record_the_geo_point-Latitude_x',
       'Walk_to_the_centre_o_record_the_geo_point-Longitude_x',
       'Walk_to_the_centre_o_record_the_geo_point-Altitude_x',
       'Walk_to_the_centre_o_record_the_geo_point-Accuracy_x',
       'Take_a_picture_of_a_ant_in_the_DEMO_PLOT',
       'Take_a_picture_of_the_DEMO_PLOT', 'geo_point-Latitude_x',
       'geo_point-Longitude_x', 'geo_point-Altitude_x', 'geo_point-Accuracy_x',
       'intercropped_x', 'primary_crop_x', 'primary_VC_photo',
       'secondary_crop_x', 'secondary_variety_x', 'secondary_VC_photo',
       'Which_inputs_have_be_since_the_last_visit',
       'Which_farm_activitie_since_the_last_visit', 'picture_field_x',
       'added_audio_info_x', 'meta-audit_x', 'meta-instanceID_x', 'KEY_x',
       'SubmitterID_x', 'SubmitterName_x', 'AttachmentsPresent_x',
       'Attac

In [ ]:
# Convert date column to a datetime object
merged_data['SubmissionDate_x'] = pd.to_datetime(merged_data['SubmissionDate_x'], format='%Y-%m-%d')


In [ ]:
merged_data = merged_data.loc[:, ['SubmissionDate_x',
        'Farmer_s_Phone_number','geo_point-Altitude_x',
       'intercropped_x', 'primary_crop_x',
       'secondary_crop_x',
       'Which_inputs_have_be_since_the_last_visit',
       'Which_farm_activitie_since_the_last_visit',
       'KEY_x', 'Gender',
       'Age_group', 'Number_of_people_in_household',
       'Number_of_children_under_5',
       'Which_DEMO_variety_has_been_issued','area_sqm',
       'polygon']]

print(merged_data)


                     SubmissionDate_x  Farmer_s_Phone_number  \
0    2022-10-14 11:39:33.338000+00:00              729099779   
1    2022-10-14 11:39:33.338000+00:00              729099779   
2    2022-10-14 11:16:04.729000+00:00              729099779   
3    2022-10-14 11:16:04.729000+00:00              729099779   
4    2022-10-14 11:38:18.854000+00:00              729657281   
...                               ...                    ...   
4256 2022-06-23 15:15:12.285000+00:00              726434908   
4257 2022-06-16 13:13:31.244000+00:00              726434908   
4258 2022-06-09 14:24:29.306000+00:00              726434908   
4259 2022-06-03 11:19:05.247000+00:00              726434908   
4260 2022-05-27 10:17:38.076000+00:00              726434908   

      geo_point-Altitude_x intercropped_x primary_crop_x secondary_crop_x  \
0              1372.500000            yes          maize            beans   
1              1372.500000            yes          maize            beans   


In [ ]:
categorical_columns = ['intercropped_x', 'primary_crop_x',
       'secondary_crop_x', 'Gender',
       'Age_group',
       'Which_DEMO_variety_has_been_issued',
       'Which_inputs_have_be_since_the_last_visit',
       'Which_farm_activitie_since_the_last_visit',
       'Which_DEMO_variety_has_been_issued']

In [ ]:
for col in categorical_columns:

    merged_data[col] = merged_data[col].astype('category')


In [ ]:
#read harvest data

harvest_data = pd.read_csv('harvest_data.csv')
harvest_data.columns

Index(['Submitter Name', 'Farmer name', 'Farmer_s_Phone_number',
       'intercropped', 'Demo variety', 'Amount Harvested in Kgs demo',
       'Primary variety', 'Amount Harvested in Kgs main', 'secondary crop',
       'Secondary variety', 'Amount Harvested  in Kgs secondary'],
      dtype='object')

In [ ]:
final_data = pd.merge(merged_data,harvest_data, on='Farmer_s_Phone_number')

In [ ]:
final_data.columns

Index(['SubmissionDate_x', 'Farmer_s_Phone_number', 'geo_point-Altitude_x',
       'intercropped_x', 'primary_crop_x', 'secondary_crop_x',
       'Which_inputs_have_be_since_the_last_visit',
       'Which_farm_activitie_since_the_last_visit', 'KEY_x', 'Gender',
       'Age_group', 'Number_of_people_in_household',
       'Number_of_children_under_5', 'Which_DEMO_variety_has_been_issued',
       'area_sqm', 'polygon', 'Submitter Name', 'Farmer name', 'intercropped',
       'Demo variety', 'Amount Harvested in Kgs demo', 'Primary variety',
       'Amount Harvested in Kgs main', 'secondary crop', 'Secondary variety',
       'Amount Harvested  in Kgs secondary'],
      dtype='object')

In [ ]:
final_data.drop(columns=['Submitter Name', 'Farmer name',
       'intercropped', 'Demo variety','Primary variety', 'secondary crop',
       'Secondary variety' ], inplace=True)
print(final_data)

                     SubmissionDate_x  Farmer_s_Phone_number  \
0    2022-08-28 14:58:06.261000+00:00              716516298   
1    2022-08-20 14:33:23.801000+00:00              716516298   
2    2022-07-30 11:03:28.219000+00:00              716516298   
3    2022-07-22 08:22:47.662000+00:00              716516298   
4    2022-07-13 08:37:37.773000+00:00              716516298   
...                               ...                    ...   
3973 2022-06-23 15:15:12.285000+00:00              726434908   
3974 2022-06-16 13:13:31.244000+00:00              726434908   
3975 2022-06-09 14:24:29.306000+00:00              726434908   
3976 2022-06-03 11:19:05.247000+00:00              726434908   
3977 2022-05-27 10:17:38.076000+00:00              726434908   

      geo_point-Altitude_x intercropped_x primary_crop_x secondary_crop_x  \
0                   1459.8             no          maize              NaN   
1                   1466.8             no          maize              NaN   


In [ ]:
df_encoded = pd.get_dummies(final_data, columns=categorical_columns, drop_first=False)


In [ ]:
df_encoded['week_number'] = df_encoded['SubmissionDate_x'].dt.week

<ipython-input-44-d353759798f6>:1: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated. Please use Series.dt.isocalendar().week instead.
  df_encoded['week_number'] = df_encoded['SubmissionDate_x'].dt.week


In [ ]:
df_encoded.columns

Index(['SubmissionDate_x', 'Farmer_s_Phone_number', 'geo_point-Altitude_x',
       'KEY_x', 'Number_of_people_in_household', 'Number_of_children_under_5',
       'area_sqm', 'polygon', 'Amount Harvested in Kgs demo',
       'Amount Harvested in Kgs main', 'Amount Harvested  in Kgs secondary',
       'intercropped_x_no', 'intercropped_x_yes', 'primary_crop_x_beans',
       'primary_crop_x_maize', 'primary_crop_x_other',
       'secondary_crop_x_beans', 'secondary_crop_x_maize',
       'secondary_crop_x_other', 'Gender_female', 'Gender_male',
       'Age_group_18___25', 'Age_group_26___35', 'Age_group_36___45',
       'Age_group_45___55', 'Age_group_above_55',
       'Which_DEMO_variety_has_been_issued_dk_777',
       'Which_DEMO_variety_has_been_issued_dkc_8083',
       'Which_DEMO_variety_has_been_issued_dkc_8089',
       'Which_DEMO_variety_has_been_issued_dkc_9089',
       'Which_inputs_have_be_since_the_last_visit_fertilizer',
       'Which_inputs_have_be_since_the_last_visit_fertil

In [ ]:
df_encoded.dtypes

SubmissionDate_x                               datetime64[ns, UTC]
Farmer_s_Phone_number                                        int64
geo_point-Altitude_x                                       float64
KEY_x                                                       object
Number_of_people_in_household                                int64
                                                      ...         
Which_DEMO_variety_has_been_issued_dk_777                    uint8
Which_DEMO_variety_has_been_issued_dkc_8083                  uint8
Which_DEMO_variety_has_been_issued_dkc_8089                  uint8
Which_DEMO_variety_has_been_issued_dkc_9089                  uint8
week_number                                                  int64
Length: 76, dtype: object

In [ ]:
#@title
import os
import re
import rasterio
import geopandas as gpd
import pandas as pd
from rasterio.mask import mask

path_to_images = '/content/drive/MyDrive/Sentinel Data'

def get_date_from_filename(filename):
    match = re.search(r'\d{8}', filename)
    if match:
        return match.group(0)
    return None

def clip_raster(raster_file, gdf, out_path):
    with rasterio.open(raster_file) as src:
        out_image, out_transform = mask(src, gdf.geometry, crop=True)
        out_meta = src.meta

    out_meta.update({
        "driver": "JP2OpenJPEG",
        "height": out_image.shape[1],
        "width": out_image.shape[2],
        "transform": out_transform
    })

    with rasterio.open(out_path, "w", **out_meta) as dest:
        dest.write(out_image)

# Read the CSV file containing farm boundaries as a GeoDataFrame
farm_boundaries = gdf_utm

# Iterate through the image files in the folder
for file in os.listdir(path_to_images):
    if file.endswith('.jp2'):
        # Extract the date from the filename
        date = get_date_from_filename(file)

        # Set output file path
        output_file = os.path.join(path_to_images, f"clipped_{file}")

        # Clip the image based on farm boundaries
        file_path = os.path.join(path_to_images, file)
        clip_raster(file_path, farm_boundaries, output_file)

        print(f"Clipped {file} and saved as {output_file}")


Clipped T37MCV_20220523T073621_AOT_10m.jp2 and saved as /content/drive/MyDrive/Sentinel Data/clipped_T37MCV_20220523T073621_AOT_10m.jp2


ValueError: ignored

In [ ]:
string_cols = df_encoded.select_dtypes(include=['object'])

In [ ]:
string_cols

KEY_x  \
0     uuid:baa51f9d-3ba0-4b5c-a6cd-7be43a821eb1   
1     uuid:d38a7201-f086-4aaa-aca8-2ef408c6ad4d   
2     uuid:45bcdde2-cfbf-4caf-b4ed-5e3056d72c3b   
3     uuid:9d255e62-7838-4d90-b40c-748e716b0da9   
4     uuid:4589c794-7845-4734-b921-449271252a87   
...                                         ...   
3973  uuid:0c49160d-47ce-45f5-96b6-1f231bd1bf6f   
3974  uuid:754b64a4-2923-4dfa-91e9-58172b7901ca   
3975  uuid:f1e5e47b-5882-4069-8d24-4bb6676cfe77   
3976  uuid:14390858-27c0-4375-b5b1-607f2c49d408   
3977  uuid:a73bcfc1-9f2e-4861-9eb3-c00e921f2896   

     Amount Harvested  in Kgs secondary  
0                                   NaN  
1                                   NaN  
2                                   NaN  
3                                   NaN  
4                                   NaN  
...                                 ...  
3973                                  0  
3974                                  0  
3975                                  0  
3976                                  0  
3977                                  0  

[3978 rows x 2 columns]

In [ ]:
# check for NaN values in each column
has_nan = df_encoded.isna().any()

# select columns with NaN values
nan_cols = df_encoded.columns[has_nan]

print(nan_cols)

Index(['Number_of_children_under_5', 'Amount Harvested in Kgs demo',
       'Amount Harvested in Kgs main', 'Amount Harvested  in Kgs secondary'],
      dtype='object')


In [ ]:
df_encoded = df_encoded.fillna(0)


In [ ]:
columns_to_convert = ['geo_point-Altitude_x', 'Number_of_people_in_household', 'Number_of_children_under_5',
       'area_sqm',
       'intercropped_x_no', 'intercropped_x_yes', 'primary_crop_x_beans',
       'primary_crop_x_maize', 'primary_crop_x_other',
       'secondary_crop_x_beans', 'secondary_crop_x_maize',
       'secondary_crop_x_other', 'Gender_female', 'Gender_male',
       'Age_group_18___25', 'Age_group_26___35', 'Age_group_36___45',
       'Age_group_45___55', 'Age_group_above_55',
       'Which_DEMO_variety_has_been_issued_dk_777',
       'Which_DEMO_variety_has_been_issued_dkc_8083',
       'Which_DEMO_variety_has_been_issued_dkc_8089',
       'Which_DEMO_variety_has_been_issued_dkc_9089',
       'Which_inputs_have_be_since_the_last_visit_fertilizer',
       'Which_inputs_have_be_since_the_last_visit_fertilizer herbicide',
       'Which_inputs_have_be_since_the_last_visit_fertilizer pesticide',
       'Which_inputs_have_be_since_the_last_visit_fertilizer pesticide herbicide',
       'Which_inputs_have_be_since_the_last_visit_fertilizer pesticide herbicide soil_enhancer',
       'Which_inputs_have_be_since_the_last_visit_herbicide',
       'Which_inputs_have_be_since_the_last_visit_none',
       'Which_inputs_have_be_since_the_last_visit_none soil_enhancer',
       'Which_inputs_have_be_since_the_last_visit_pesticide',
       'Which_inputs_have_be_since_the_last_visit_pesticide fertilizer',
       'Which_inputs_have_be_since_the_last_visit_pesticide fertilizer herbicide',
       'Which_inputs_have_be_since_the_last_visit_pesticide soil_enhancer',
       'Which_inputs_have_be_since_the_last_visit_soil_enhancer',
       'Which_inputs_have_be_since_the_last_visit_soil_enhancer none',
       'Which_farm_activitie_since_the_last_visit_no_activity',
       'Which_farm_activitie_since_the_last_visit_no_activity option_4',
       'Which_farm_activitie_since_the_last_visit_option_4',
       'Which_farm_activitie_since_the_last_visit_option_4 supplementary_irrigation',
       'Which_farm_activitie_since_the_last_visit_option_4 weeding',
       'Which_farm_activitie_since_the_last_visit_option_4 weeding top_dressing',
       'Which_farm_activitie_since_the_last_visit_planting',
       'Which_farm_activitie_since_the_last_visit_planting option_4',
       'Which_farm_activitie_since_the_last_visit_planting top_dressing',
       'Which_farm_activitie_since_the_last_visit_planting top_dressing option_4 weeding',
       'Which_farm_activitie_since_the_last_visit_planting top_dressing weeding option_4',
       'Which_farm_activitie_since_the_last_visit_planting weeding',
       'Which_farm_activitie_since_the_last_visit_planting weeding option_4 top_dressing',
       'Which_farm_activitie_since_the_last_visit_planting weeding top_dressing',
       'Which_farm_activitie_since_the_last_visit_planting weeding top_dressing option_4',
       'Which_farm_activitie_since_the_last_visit_supplementary_irrigation',
       'Which_farm_activitie_since_the_last_visit_supplementary_irrigation option_4',
       'Which_farm_activitie_since_the_last_visit_supplementary_irrigation option_4 top_dressing',
       'Which_farm_activitie_since_the_last_visit_top_dressing',
       'Which_farm_activitie_since_the_last_visit_top_dressing option_4',
       'Which_farm_activitie_since_the_last_visit_top_dressing option_4 weeding',
       'Which_farm_activitie_since_the_last_visit_top_dressing weeding option_4',
       'Which_farm_activitie_since_the_last_visit_weeding',
       'Which_farm_activitie_since_the_last_visit_weeding option_4',
       'Which_farm_activitie_since_the_last_visit_weeding option_4 top_dressing',
       'Which_farm_activitie_since_the_last_visit_weeding top_dressing',
       'Which_farm_activitie_since_the_last_visit_weeding top_dressing option_4',
       'Which_DEMO_variety_has_been_issued_dk_777',
       'Which_DEMO_variety_has_been_issued_dkc_8083',
       'Which_DEMO_variety_has_been_issued_dkc_8089',
       'Which_DEMO_variety_has_been_issued_dkc_9089', 'week_number']

df_list = df_encoded[columns_to_convert].values.tolist()

In [ ]:
import numpy as np

# Convert the flattened features and other features into a single feature array
features = np.array(df_list)


In [ ]:
from sklearn.model_selection import train_test_split

# Define the input features and target variable
X = features
y = df_encoded['Amount Harvested in Kgs main']

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [ ]:
# sklearn models
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.svm import SVR
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

# fastai
from fastai.tabular.all import *


In [ ]:
models = [
    ('RandomForest', RandomForestRegressor(n_estimators=100, random_state=42)),
    ('LinearRegression', LinearRegression()),
    ('Ridge', Ridge(alpha=1)),
    ('Lasso', Lasso(alpha=1)),
    ('GradientBoosting', GradientBoostingRegressor(random_state=42)),
    ('XGBoost', XGBRegressor(random_state=42)),
    ('LightGBM', LGBMRegressor(random_state=42))
]

In [ ]:
from sklearn.metrics import mean_squared_error, r2_score, accuracy_score
from math import sqrt

def evaluate_model(model, X_train, X_test, y_train, y_test):
    # Train the model
    model.fit(X_train, y_train)

    # Make predictions using the testing data
    y_pred = model.predict(X_test)

    # Calculate evaluation metrics
    rmse = sqrt(mean_squared_error(y_test, y_pred))
    r2 = r2_score(y_test, y_pred)


    return rmse, r2


In [ ]:
# Iterate over the models list and evaluate each model
for model_name, model in models:
    mse, r2 = evaluate_model(model, X_train, X_test, y_train, y_test)
    print(f"{model_name}: MSE = {mse}, R2 = {r2}")


RandomForest: MSE = 18.270385846910155, R2 = 0.9470079268929774
LinearRegression: MSE = 76.10824373078366, R2 = 0.08044253968163595
Ridge: MSE = 76.0514812105312, R2 = 0.08181366407052115
Lasso: MSE = 76.76662490415745, R2 = 0.06446429851075541


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.06209e-19): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T


GradientBoosting: MSE = 45.533327087919645, R2 = 0.6708648678929592
XGBoost: MSE = 16.965970219649154, R2 = 0.9543045590794299
LightGBM: MSE = 29.21324321113762, R2 = 0.8645200523043304


In [ ]:
#create season 2 data

# Read the CSV file
df2 = pd.read_csv('onboarding2.csv')
df2.head()

SubmissionDate                          start  \
0  2023-01-26T08:25:23.334Z  2023-01-26T11:21:29.033+03:00   
1  2022-11-24T12:48:39.710Z  2022-11-24T15:35:11.627+03:00   
2  2022-11-19T07:28:53.110Z  2022-11-19T08:53:56.229+03:00   
3  2022-11-18T13:52:02.805Z  2022-11-18T16:42:32.360+03:00   
4  2022-11-18T13:04:44.815Z  2022-11-18T15:47:01.458+03:00   

                             end            username  \
0  2023-01-26T11:25:18.795+03:00                 NaN   
1  2022-11-29T12:20:16.355+03:00  username not found   
2  2022-11-19T10:28:42.254+03:00                 NaN   
3  2022-11-18T16:49:09.613+03:00                 NaN   
4  2022-11-18T16:03:21.644+03:00                 NaN   

                   deviceid            phonenumber Consent    Farmer_name  \
0  collect:5oC6liKX0JjuZG9k                    NaN      OK           Test   
1  collect:mtlWndOdiuKDDuRB  phonenumber not found      OK  Vitalist Thuo   
2  collect:pvcWh1uzLaOiCiUJ                    NaN      OK    Susan Njeri   
3  collect:J0HuuQuHlK9Y45NA                    NaN      OK     Rosa wanja   
4  collect:mtlWndOdiuKDDuRB                    NaN      OK  Samuel Njogo    

   Gender Age_group  ...                            meta-instanceID  \
0   other  above_55  ...  uuid:6c28fe70-efa6-4104-9728-a57838b6065c   
1    male   26___35  ...  uuid:fce6b4c6-59b4-44d2-9a52-293f03a4c2a5   
2  female   36___45  ...  uuid:e2c50d3d-15b5-4fdd-8a38-a9f43869f3da   
3  female   36___45  ...  uuid:0fd665b9-4d6a-4eaf-8f16-6c8e12a382e8   
4    male   45___55  ...  uuid:588e947f-017f-4dd5-b318-f7a734edfba4   

                                         KEY  SubmitterID  \
0  uuid:6c28fe70-efa6-4104-9728-a57838b6065c           87   
1  uuid:05372465-aa91-4f49-afda-f94f5acd68f0           71   
2  uuid:e2c50d3d-15b5-4fdd-8a38-a9f43869f3da           75   
3  uuid:0fd665b9-4d6a-4eaf-8f16-6c8e12a382e8           87   
4  uuid:588e947f-017f-4dd5-b318-f7a734edfba4           71   

            SubmitterName  AttachmentsPresent  AttachmentsExpected  Status  \
0  Virginia Makena Muguna                   3                    3     NaN   
1      Martha Murugi Thuo                   7                    7     NaN   
2            Esther Mburu                   5                    5     NaN   
3  Virginia Makena Muguna                   5                    5     NaN   
4      Martha Murugi Thuo                   7                    7     NaN   

  ReviewState                  DeviceID Edits  
0    rejected  collect:5oC6liKX0JjuZG9k     0  
1      edited  collect:mtlWndOdiuKDDuRB     1  
2         NaN  collect:pvcWh1uzLaOiCiUJ     0  
3         NaN  collect:J0HuuQuHlK9Y45NA     0  
4         NaN  collect:mtlWndOdiuKDDuRB     0  

[5 rows x 49 columns]

In [ ]:
# Get unique values in a specific column
unique_values = df['ReviewState'].unique()

# Print the unique values
print(unique_values)


# Explore the Satellite Imagery

In [ ]:
pip install rasterio geopandas pandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 44.6 MB/s eta 0:00:00
